In [3]:
# Import the data
import pandas as pd
import re
from nltk import sent_tokenize

df = pd.read_excel('External Data/Training-Restated.xlsx')

# Convert to date


df['Completion Date'] = pd.to_datetime(df['Completion Date'], origin='1899-12-30', unit='D', errors='coerce')
#df['Match Activation Date'] = pd.to_datetime(df['Match Activation Date'], origin='1899-12-30', unit='D', errors='coerce')
#df['Match Closure Meeting Date'] = pd.to_datetime(df['Match Closure Meeting Date'], origin='1899-12-30', unit='D', errors='coerce')
#df['Little Birthdate'] = pd.to_datetime(df['Little Birthdate'], origin='1899-12-30', unit='D', errors='coerce')
#df['Big Birthdate'] = pd.to_datetime(df['Big Birthdate'], origin='1899-12-30', unit='D', errors='coerce')
#df['Big Approved Date'] = pd.to_datetime(df['Big Approved Date'], origin='1899-12-30', unit='D', errors='coerce')


# Sort the data
df_sorted = df.sort_values(by=['Match ID 18Char', 'Completion Date'], ascending=[True, True])

# Fill Empty Data 
df_sorted['Match Support Contact Notes'] = df_sorted['Match Support Contact Notes'].fillna('No Updates').astype(str)
df_sorted = df_sorted.groupby('Match ID 18Char').tail(10)
df_sorted.head()

# Tokenizer to shorten sentences as well as remove unwanted stuff like URLs and spaces

def shorten_text(text):
    # Remove URLs
    text = re.sub(r'http[s]?://[^\s]+', '', text)
    # Replace multiple spaces with a single space
    text = re.sub(r'\s+', ' ', text).strip()
    # Remove sequences of underscores longer than 3
    text = re.sub(r'_{4,}', '', text)
    
    # Split into dated blocks
    blocks = text.split('\n\n')
    shortened_blocks = []
    
    for block in blocks:
        # Extract the date (assuming YYYY-MM-DD format)
        match = re.match(r'(\d{4}-\d{2}-\d{2})', block)
        if not match:
            continue
        date = match.group(1)
        content = block[len(date):].strip()
        
        # Split content into lines
        lines = content.split('\n')
        filtered_lines = []
        
        for line in lines:
            if "Answer:" in line:
                question, answer = line.split("Answer:", 1)
                answer = answer.strip()
                if answer.lower() not in ['na', 'n/a', '-', '_', '__', '___', '']:
                    filtered_lines.append(f"{question.strip()} Answer: {answer}")
            else:
                filtered_lines.append(line.strip())
        
        if not filtered_lines:
            shortened_content = content.split('\n')[0]
        else:
            combined_content = ' '.join(filtered_lines)
            sentences = sent_tokenize(combined_content)
            key_sentences = [s for s in sentences if "See notes" not in s][:2]
            shortened_content = ' '.join(key_sentences) if key_sentences else combined_content.split('\n')[0]
        
        shortened_blocks.append(f"{date} {shortened_content}")
    
    return '\n\n'.join(shortened_blocks) if shortened_blocks else text.split('\n\n')[0]


# Ensure 'Completion Date' is in datetime format
df_sorted['Completion Date'] = pd.to_datetime(df_sorted['Completion Date'], errors='coerce')
df_sorted['Short Notes'] = df_sorted['Match Support Contact Notes'].apply(shorten_text)
df_sorted['Dated Short Notes'] = df_sorted['Completion Date'].astype(str) + ' ' + df_sorted['Short Notes'].fillna('').astype(str)

# Group by 'Match ID 18Char' and combine dated notes
flat_df = df_sorted.groupby('Match ID 18Char')['Dated Short Notes'].agg(lambda x: '\n\n'.join(x)).reset_index()
flat_df.columns = ['Match ID 18Char', 'Dated Short Notes']

# Display the result
print(flat_df.head(5))



      Match ID 18Char                                  Dated Short Notes
0  a1v2J0000027CWYQA2  2017-03-23 Question: Activities: Answer: BS as...
1  a1v2J0000027CWfQAM  2017-02-08 Question: Activities: Answer: Sami ...
2  a1v2J0000027CWiQAM  2017-02-15 Question: Activities: Answer: BS ha...
3  a1v2J0000027CWoQAM  2017-03-28 Question: Activities: Answer: BS pl...
4  a1v2J0000027CWpQAM  2017-02-08 Question: Activities: Answer: B_fir...


In [4]:
# Now do the same thing for match reason 

def is_non_blank(note):
    return pd.notna(note) and str(note).strip() != ""

# Filter rows with non-blank notes and group by Match ID, taking the first entry
match_rationale_df = (df[df["Rationale for Match"].apply(is_non_blank)]
          .groupby("Match ID 18Char", as_index=False)
          .agg({"Rationale for Match": "first"}))

match_rationale_df['Rationale for Match'] = match_rationale_df['Rationale for Match'].apply(shorten_text)


# Identify the first column names (assuming they are the same, e.g., "Match ID 18Char")
match_id_col_rationale = match_rationale_df.columns[0]
match_id_col_flat = flat_df.columns[0]


# Step 3: Merge with flat_df
merged_df = match_rationale_df.merge(
    flat_df,
    how="outer",  # Use outer join to retain all Match IDs from both DFs
    left_on=match_id_col_rationale,
    right_on=match_id_col_flat
)

# Remove duplicate Match ID columns if they exist
merged_df = merged_df.loc[:, ~merged_df.columns.duplicated()]

# Display the resulting DataFrame
print(merged_df.head(5))

merged_df.to_excel('Apr3TrainRun1.xlsx', index=False)

      Match ID 18Char                                Rationale for Match  \
0  a1v2J0000027CWsQAM  Both are female and Karen and have an understa...   
1  a1v2J0000027CX1QAM  Already matched. LS transferred school but MC ...   
2  a1v2J0000027CXHQA2  Both are female, share similarities, and will ...   
3  a1v2J0000027GURQA2  Both share similar interests and distance was ...   
4  a1v2J0000027GVZQA2  L_first_name and B_first_name both enjoy girly...   

                                   Dated Short Notes  
0  2017-12-20 Question: Activities: Answer: BS an...  
1  2017-11-06 Question: Activities: Answer: The m...  
2  2017-12-20 Question: Activities: Answer: The m...  
3  2018-08-14 Question: Activities: Answer: MEC i...  
4  2021-01-25 BS replied to check in email as wel...  


In [7]:


import os
from openai import OpenAI
import json
from typing import List, Dict, Any
from IPython.display import display, JSON  # For nice JSON display in Jupyter

os.environ["XAI_API_KEY"] = "xai-5q7CtzPajDnu5Ucaic4kCbaMXcskpnYt2In72q49rGBrM49T10gZ0kCkTsAVw0hqrnoY2kbszKNg7IlK"

context = '''
Primary Task:
You are to process text and identify potential events in the mentorship program by Big Brothers Big Sisters of America. Your sole purpose is to classify the identified events as either Green Flags (positive indicators) or Red Flags (negative indicators).

Definitions:
BBB or Agency = Big brothers’ big sisters of America organization
LB/LS = Little Brother/Sister (Mentee Or Child)
BB/BS = Big Brother/Sister (Mentor Or Volunteer)
MEC or MSC = Match coordinator from BBB
PG = Parent of LB/LS
Current Service area = Minnesota

Flags :
Green Flags: Factors likely to enhance relationship quality and increase the duration of the match.
Red Flags: Risks or factors that may lead to early termination or poor outcomes in the match.

Green Flags are:
Identify any event that aligns with one or more of the following factors, which indicate a positive match:
Rationale for Match: Any event that contributes positively to the rationale behind the match.
Pre-Match Training: The mentor has completed BBB training before the match.
Commitment to 18-Month Match Duration: The mentor has committed to at least an 18-month match duration.
Shared Interests/Preferences: Mentor and mentee have shared interests or preferences that align.
Monthly In-Person/Phone Support: Monthly support is provided by the agency to the mentor, youth, and parent (via in-person or phone).
High Mentor Satisfaction: Mentor reports satisfaction with the match and has realistic expectations about the relationship.
Positive Youth Reports: The youth reports a positive relationship with the mentor and frequent meetings.
Demographic Alignment: The match has alignment in terms of race, gender, or religion.
Close Geographic Proximity/Transportation: Mentor and mentee live in close geographic proximity or have good transportation access.
Positive Youth Traits: The youth displays positive traits like competence, confidence, connection, care, and character.
Experienced Mentor: The mentor is older, experienced, and demonstrates empathy, flexibility, and multicultural competence.
Younger Mentee (elementary–early adolescence): The mentee is in the younger age group (elementary to early adolescence) and has a good relational history.

Red Flags are:
No Pre-Match Training or Ongoing Support: If the mentor has not received pre-match training or ongoing support.
Mismatched Interests/Preferences: The mentor’s preferences are ignored, or there is a significant mismatch in interests.
Infrequent/Surface-Level Staff Check-ins: Staff check-ins are infrequent or too short (less than 6 minutes).
Mentor Frustration/Unrealistic Expectations: If the mentor expresses frustration, has unrealistic expectations, or there is significant youth resistance.
No Closure Plan for Early Termination: There is no closure plan in place for when the match ends prematurely.
Match Ends in Less Than 6 Months: The match duration is less than 6 months (34–50% risk of early termination).
Younger Mentor (18–25) with Negative Attitudes: The mentor is younger (18–25 years old) and demonstrates negative attitudes or low commitment.
Older Mentee Seeking Autonomy: The mentee is older and is seeking autonomy, presenting severe risk factors.
No Monthly Support (Email-Only Contact): The match does not receive monthly support from the agency or only has email contact.
Excessive/Scanty Staff Involvement: The mentor receives inadequate training, or the staff involvement is either excessive or insufficient.
Parental Dissatisfaction/Interference: The parent or guardian of the mentee expresses dissatisfaction or interferes with the match.
Match Ends Before 13–18 Months: The match ends prematurely (before the 13–18 months mark).
'''

output = '''
Response Guidance
Events to Detect (Used Exclusively for JSON "events" Field):
(Ensure detected events are exactly as listed below)

Events To Detect:

Match closure Discussed,
Changing Match Type,
COVID impact,
Child/Family: Feels incompatible with volunteer,
Child/Family: Moved,
Child/Family: Lost contact with agency,
Child/Family: Lost contact with volunteer/agency,
Child/Family: Lost contact with volunteer,
Child/Family: Moved out of service,
Child/Family: Unrealistic expectations,
Child/Family: Time constraints,
Child/Family: Infraction of match rules/agency policies,
Child/Family: Moved within service area,
Child/Family: Amidst divorce,
Child: Graduated,
Child: Transportation Issues,
Child: Changed school/site,
Child: Lost interest,
Child: Family structure changed,
Child: Severity of challenges,
Volunteer: Transportation Issues,
Volunteer: Moved out of service area,
Volunteer: Moved within service area,
Volunteer: Lost contact with agency,
Volunteer: Lost contact with child/agency,
Volunteer: Feels incompatible with child/family,
Volunteer: Time constraints,
Volunteer: Deceased,
Volunteer: Lost contact with child/family,
Volunteer: Infraction of match rules/agency policies,
Volunteer: Unrealistic expectations,
Volunteer: Pregnancy,
Volunteer: Changed workplace/school partnership,
Volunteer: Amidst divorce,
Agency: Challenges with program/partnership,
Agency: Concern with Volunteer re: child safety
End Events To Detect

JSON Response Format (Strictly Follow This Structure)

Always return a valid JSON object containing:
green_flag_count: Number of detected green flag (if any)
red_flag_count: Number of detected red flag
events: A dictionary where:
Keys are detected event names (must match exactly from the provided list (Events To Detect)
Values are assigned severity scores (1–5) where 5 will lead to a imminent match termination
Each event should carry on to the later dates unless it is mentioned and resolved in the later date!
No not include positive events, only those events from above (Events To Detect:)
No other text except the JSON!

Example JSON Response:
[
  {
    "date" : "2025/04/30"
    "green_flag_count": 2,
    "red_flag_count": 3,
    "events": {
      "Child/Family: Unrealistic expectations": 3,
      "Volunteer: Unrealistic expectations": 4,
      "Agency: Concern with Volunteer re: child safety": 5
    }
  }
]
'''

count = 0;

def parse_json_message(json_string: str) -> List[Dict[str, Any]]:
    
    try:
        brace_position = json_string.index('[')
        json_string = json_string[brace_position:]
    except:
        raise ValueError("Input does not start with '[': invalid JSON array format.")

    while True:
        if not json_string:
            raise ValueError("Couldn't fix JSON")
        try:
            data = json.loads(json_string + "]")
        except json.decoder.JSONDecodeError:
            json_string = json_string[:-1]
            continue
        break
    return data

def process_row(row: pd.Series, error_df: pd.DataFrame) -> List[Dict[str, Any]]:
    rationale = row["Rationale for Match"]
    query = row["Dated Short Notes"]
    matchid = row["Match ID 18Char"]
    
    try:
        # Assume process_grok_queries returns a JSON string
        json_response = process_grok_queries("Rationale For March " + str(rationale) + " Dated Short Notes : " + str(query))
        parsed_response = parse_json_message(json_response)
        
        print("------------------------------")
    
        return parsed_response
    except (ValueError, json.JSONDecodeError) as e:
 
        error_row = pd.DataFrame({
            "Match ID 18Char": [matchid],
            "Rationale for Match": [rationale],
            "Dated Short Notes": [query],
            "Error": [str(e)]
        })

        globals()["error_df"] = pd.concat([error_df, error_row], ignore_index=True)
        return None
    
            
def process_grok_queries(query_str):
    global count
    # Retrieve the API key from the environment variable
    api_key = os.getenv("XAI_API_KEY")
    if not api_key:
        raise ValueError("XAI_API_KEY environment variable is not set.")
        
    # Initialize the OpenAI client with the Grok API base URL and API key
    client = OpenAI(
        api_key=api_key,
        base_url="https://api.x.ai/v1"
    )
    
    user_content = str(context) + " Dated Match Notes: " + str(query_str) + output
    
    cached_context = {
        "role": "system",
        "content": context
    }
    
    messages = [
    cached_context,
        {"role": "user", "content": query_str + output}
    ]
    
    # Make API call!!
    response = client.chat.completions.create(
        model="grok-2-latest",
        messages=messages,
        max_tokens=1000
    )
    
    # Decode the data 
    count+=1
    answer = response.choices[0].message.content  
    
    print("Processed: " + str(count))
    print("------------------------------")
    print(answer)
    
    token_count = response.usage.total_tokens if response.usage else 0
    print("------------------------------")
    print("Token Count: " + str(token_count))

    return answer

# Process the query str column !

error_df = pd.DataFrame(columns=["Match ID 18Char", "Rationale for Match", "Dated Short Notes", "Error"])  # To store errors with matchid

# Process each row and handle errors
merged_df["JSON Response"] = merged_df.apply(
    lambda row: process_row(row, error_df), axis=1
)
merged_df.to_excel('Apr3TrainRun1LLM.xlsx', index=False)

Processed: 1
------------------------------
[
  {
    "date": "2017-12-20",
    "green_flag_count": 2,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2018-01-19",
    "green_flag_count": 2,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2018-02-18",
    "green_flag_count": 2,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2018-03-20",
    "green_flag_count": 2,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2018-04-19",
    "green_flag_count": 2,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2018-05-16",
    "green_flag_count": 2,
    "red_flag_count": 0,
    "events": {
      "Child: Graduated": 3
    }
  },
  {
    "date": "2018-06-14",
    "green_flag_count": 2,
    "red_flag_count": 0,
    "events": {
      "Child: Graduated": 3
    }
  },
  {
    "date": "2018-06-15",
    "green_flag_count": 2,
    "red_flag_count": 0,
    "events": {
      "Child: Graduated": 3
    }
  }
]
----------------------

Processed: 9
------------------------------
[
  {
    "date": "2019-07-18",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2019-09-20",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2019-11-20",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2020-01-31",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2020-04-29",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {
      "COVID impact": 2
    }
  },
  {
    "date": "2020-07-20",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {
      "COVID impact": 2
    }
  },
  {
    "date": "2020-10-07",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {
      "COVID impact": 2,
      "Volunteer: Lost contact with child/family": 3
    }
  },
  {
    "date": "2021-01-21",
    "green_flag_count": 0,
    "red_flag_count": 0,
   

Processed: 17
------------------------------
[
  {
    "date": "2018-02-28",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2018-03-26",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2018-05-25",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2018-08-10",
    "green_flag_count": 0,
    "red_flag_count": 1,
    "events": {
      "Match closure Discussed": 3
    }
  },
  {
    "date": "2018-09-06",
    "green_flag_count": 0,
    "red_flag_count": 1,
    "events": {
      "Match closure Discussed": 3
    }
  }
]
------------------------------
Token Count: 2410
------------------------------
Processed: 18
------------------------------
[
  {
    "date": "2018-11-30",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2018-12-10",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "

Processed: 26
------------------------------
[
  {
    "date": "2019-04-12",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2019-06-20",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2019-08-19",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2019-09-29",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2019-11-15",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2020-02-18",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {
      "Changing Match Type": 2
    }
  },
  {
    "date": "2020-05-06",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {
      "COVID impact": 3,
      "Changing Match Type": 2
    }
  },
  {
    "date": "2020-08-14",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {
      "COVID impact": 3,
     

Processed: 36
------------------------------
```json
[
  {
    "date": "2019-03-21",
    "green_flag_count": 1,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2019-04-25",
    "green_flag_count": 2,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2019-06-03",
    "green_flag_count": 2,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2019-08-05",
    "green_flag_count": 2,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2019-12-11",
    "green_flag_count": 3,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2019-12-17",
    "green_flag_count": 3,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2020-03-10",
    "green_flag_count": 3,
    "red_flag_count": 0,
    "events": {
      "Changing Match Type": 2
    }
  },
  {
    "date": "2020-11-16",
    "green_flag_count": 3,
    "red_flag_count": 0,
    "events": {
      "COVID impact": 3,
      "Changing Match Type": 2
    }
  },
  {
    "date": 

...

Processed: 3248
------------------------------
[
  {
    "date": "2017-04-25",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2017-06-22",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2017-08-09",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2017-09-12",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {}
  }
]
------------------------------
Token Count: 3099
------------------------------
Processed: 3249
------------------------------
[
  {
    "date": "2017-08-08",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2017-09-19",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2017-10-19",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2017-11-17",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events

Processed: 3256
------------------------------
[
  {
    "date": "2022-11-01",
    "green_flag_count": 0,
    "red_flag_count": 1,
    "events": {
      "Child/Family: Lost contact with agency": 2
    }
  },
  {
    "date": "2023-02-03",
    "green_flag_count": 0,
    "red_flag_count": 1,
    "events": {
      "Child/Family: Lost contact with agency": 2
    }
  },
  {
    "date": "2023-05-11",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2023-08-07",
    "green_flag_count": 0,
    "red_flag_count": 1,
    "events": {
      "Child: Lost interest": 3
    }
  },
  {
    "date": "2023-08-31",
    "green_flag_count": 0,
    "red_flag_count": 2,
    "events": {
      "Child/Family: Lost contact with agency": 3,
      "Child/Family: Moved within service area": 2
    }
  },
  {
    "date": "2023-11-27",
    "green_flag_count": 0,
    "red_flag_count": 2,
    "events": {
      "Child/Family: Lost contact with agency": 3,
      "Child/Family: Moved w

Processed: 3262
------------------------------
[
  {
    "date": "2017-03-31",
    "green_flag_count": 4,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2017-08-12",
    "green_flag_count": 4,
    "red_flag_count": 0,
    "events": {}
  }
]
------------------------------
Token Count: 1701
------------------------------
Processed: 3263
------------------------------
[
  {
    "date": "2017-04-26",
    "green_flag_count": 3,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2017-07-10",
    "green_flag_count": 2,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2017-08-31",
    "green_flag_count": 3,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2017-09-06",
    "green_flag_count": 4,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2017-12-19",
    "green_flag_count": 3,
    "red_flag_count": 0,
    "events": {
      "Volunteer: Transportation Issues": 2
    }
  },
  {
    "date": "2018-02-06",
    "green_fla

Processed: 3269
------------------------------
[
  {
    "date": "2018-08-28",
    "green_flag_count": 1,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2019-01-08",
    "green_flag_count": 0,
    "red_flag_count": 0,
    "events": {
      "Child/Family: Lost contact with volunteer": 3
    }
  },
  {
    "date": "2019-04-26",
    "green_flag_count": 1,
    "red_flag_count": 0,
    "events": {
      "Child/Family: Lost contact with volunteer": 3
    }
  },
  {
    "date": "2019-07-11",
    "green_flag_count": 1,
    "red_flag_count": 0,
    "events": {
      "Child/Family: Lost contact with volunteer": 3
    }
  },
  {
    "date": "2019-10-31",
    "green_flag_count": 1,
    "red_flag_count": 0,
    "events": {
      "Child/Family: Lost contact with volunteer": 3
    }
  },
  {
    "date": "2020-02-05",
    "green_flag_count": 1,
    "red_flag_count": 0,
    "events": {
      "Child/Family: Lost contact with volunteer": 3
    }
  },
  {
    "date": "2020-05-21",
    "gr

Processed: 3274
------------------------------
[
  {
    "date": "2018-10-04",
    "green_flag_count": 2,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2018-11-29",
    "green_flag_count": 2,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2019-02-19",
    "green_flag_count": 2,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2019-05-14",
    "green_flag_count": 2,
    "red_flag_count": 0,
    "events": {}
  },
  {
    "date": "2019-08-23",
    "green_flag_count": 2,
    "red_flag_count": 1,
    "events": {
      "Volunteer: Time constraints": 3
    }
  },
  {
    "date": "2019-12-03",
    "green_flag_count": 2,
    "red_flag_count": 1,
    "events": {
      "Volunteer: Time constraints": 3
    }
  },
  {
    "date": "2020-04-22",
    "green_flag_count": 2,
    "red_flag_count": 1,
    "events": {
      "Volunteer: Time constraints": 3,
      "COVID impact": 2
    }
  },
  {
    "date": "2020-08-24",
    "green_flag_count": 2,
    "red_

In [10]:

import ast

columns = [
    'Match closure Discussed',
    'Changing Match Type',
    'COVID impact',
    'Child/Family: Feels incompatible with volunteer',
    'Child/Family: Moved',
    'Child/Family: Lost contact with agency',
    'Child/Family: Lost contact with volunteer/agency',
    'Child/Family: Lost contact with volunteer',
    'Child/Family: Moved out of service',
    'Child/Family: Unrealistic expectations',
    'Child/Family: Time constraints',
    'Child/Family: Infraction of match rules/agency policies',
    'Child/Family: Moved within service area',
    'Child/Family: Amidst divorce',
    'Child: Graduated',
    'Child: Transportation Issues',
    'Child: Changed school/site',
    'Child: Lost interest',
    'Child: Family structure changed',
    'Child: Severity of challenges',
    'Volunteer: Transportation Issues',
    'Volunteer: Moved out of service area',
    'Volunteer: Moved within service area',
    'Volunteer: Lost contact with agency',
    'Volunteer: Lost contact with child/agency',
    'Volunteer: Feels incompatible with child/family',
    'Volunteer: Time constraint',
    'Volunteer: Deceased',
    'Volunteer: Lost contact with child/family',
    'Volunteer: Infraction of match rules/agency policies',
    'Volunteer: Unrealistic expectations',
    'Volunteer: Pregnancy',
    'Volunteer: Amidst divorce',
    'Volunteer: Changed workplace/school partnership',
    'Agency: Challenges with program/partnership',
    'Agency: Concern with Volunteer re: child safety'
    
]

df_json = pd.read_excel('Apr3TrainRun1LLM.xlsx')


def parse_json_response(json_str):
    if pd.isna(json_str) or not json_str:
        return [] 
    if isinstance(json_str, str):
        return ast.literal_eval(json_str)  
    return json_str 

df_json['JSON Response'] = df_json['JSON Response'].apply(parse_json_response)

df_exploded = df_json.explode('JSON Response').reset_index(drop=True)

df_exploded['date'] = df_exploded['JSON Response'].apply(
    lambda x: x['date'] if isinstance(x, dict) and 'date' in x else pd.NA
)

# Step 4: Display the result
print(df_exploded)
df_exploded.to_excel('Apr3TrainRun1LLMExploded.xlsx', index=False)

          Match ID 18Char                                Rationale for Match  \
0      a1v2J0000027CWsQAM  Both are female and Karen and have an understa...   
1      a1v2J0000027CWsQAM  Both are female and Karen and have an understa...   
2      a1v2J0000027CWsQAM  Both are female and Karen and have an understa...   
3      a1v2J0000027CWsQAM  Both are female and Karen and have an understa...   
4      a1v2J0000027CWsQAM  Both are female and Karen and have an understa...   
...                   ...                                                ...   
25045  a1v2J0000038jRgQAI                                                NaN   
25046  a1v2J0000038jRgQAI                                                NaN   
25047  a1v2J0000038jRgQAI                                                NaN   
25048  a1v2J0000038jRgQAI                                                NaN   
25049  a1v2J0000038jRgQAI                                                NaN   

                                       

      Match ID 18Char        date  green_flag_count  red_flag_count  \
0  a1v2J0000027dtOQAQ  2024-04-04                 4               0   
1  a1v2J0000027dtOQAQ  2024-07-10                 2               0   
2  a1v2J0000027dtOQAQ  2024-10-07                 1               1   
3  a1v2J0000027dtOQAQ  2025-01-14                 0               2   
4  a1v2J0000027dtOQAQ  2025-02-13                 0               1   
5  a1v2J000002uR0JQAU  2022-02-11                 1               5   
6  a1v2J0000028pRvQAI  2017-10-11                 3               0   
7  a1v2J0000028pRvQAI  2017-10-31                 0               2   
8  a1v2J0000028pRvQAI  2017-11-30                 0               1   
9  a1v2J0000028pRvQAI  2017-12-01                 0               1   

                                              events  
0  {'Child/Family: Time constraints': 1, 'Volunte...  
1  {'Child/Family: Time constraints': 1, 'Volunte...  
2  {'Child/Family: Time constraints': 2, 'Volunte... 

In [4]:
import pandas as pd
import ast

columns = [
    'Match closure Discussed',
    'Changing Match Type',
    'COVID impact',
    'Child/Family: Feels incompatible with volunteer',
    'Child/Family: Moved',
    'Child/Family: Lost contact with agency',
    'Child/Family: Lost contact with volunteer/agency',
    'Child/Family: Lost contact with volunteer',
    'Child/Family: Moved out of service',
    'Child/Family: Unrealistic expectations',
    'Child/Family: Time constraints',
    'Child/Family: Infraction of match rules/agency policies',
    'Child/Family: Moved within service area',
    'Child/Family: Amidst divorce',
    'Child: Graduated',
    'Child: Transportation Issues',
    'Child: Changed school/site',
    'Child: Lost interest',
    'Child: Family structure changed',
    'Child: Severity of challenges',
    'Volunteer: Transportation Issues',
    'Volunteer: Moved out of service area',
    'Volunteer: Moved within service area',
    'Volunteer: Lost contact with agency',
    'Volunteer: Lost contact with child/agency',
    'Volunteer: Feels incompatible with child/family',
    'Volunteer: Time constraint',
    'Volunteer: Deceased',
    'Volunteer: Lost contact with child/family',
    'Volunteer: Infraction of match rules/agency policies',
    'Volunteer: Unrealistic expectations',
    'Volunteer: Pregnancy',
    'Volunteer: Amidst divorce',
    'Volunteer: Changed workplace/school partnership',
    'Agency: Challenges with program/partnership',
    'Agency: Concern with Volunteer re: child safety'
]

df = pd.read_excel('Apr3TrainRun1LLM.xlsx')  

# Function to parse 'JSON Response' safely
def parse_json_response(json_str):
    if pd.isna(json_str) or not json_str:
        return []  # Handle NaN or empty values
    if isinstance(json_str, str):
        try:
            return ast.literal_eval(json_str)  # Convert string to Python list
        except (ValueError, SyntaxError) as e:
            print(f"Error parsing JSON Response: {json_str} - {e}")
            return []
    return json_str  # If already a list, return as is

# Apply parsing to 'JSON Response' column
df['JSON Response'] = df['JSON Response'].apply(parse_json_response)

# Step 1: Explode the 'JSON Response' list into separate rows
df_exploded = df.explode('JSON Response').reset_index(drop=True)

# Step 2: Flatten the JSON Response with error handling
def flatten_json_row(row):
    if isinstance(row['JSON Response'], dict):
        # Extract base fields
        base_data = {
            'date': row['JSON Response'].get('date', pd.NA),
            'green_flag_count': row['JSON Response'].get('green_flag_count', 0),
            'red_flag_count': row['JSON Response'].get('red_flag_count', 0)
        }
        # Extract events dictionary, default to empty dict if missing
        events = row['JSON Response'].get('events', {})
        # Create a dictionary with all event columns, defaulting to 0
        event_data = {col: events.get(col, 0) for col in columns}
        return pd.Series({**base_data, **event_data})
    else:
        # Default row for non-dict entries
        print(f"Non-dict found for Match ID {row['Match ID 18Char']}: {row['JSON Response']}")
        return pd.Series(
            {'date': pd.NA, 'green_flag_count': 0, 'red_flag_count': 0, **{col: 0 for col in columns}}
        )

# Step 3: Apply flattening to each row
flat_df = df_exploded.apply(flatten_json_row, axis=1)

# Step 4: Combine with 'Match ID 18Char'
df_final = pd.concat([df_exploded[['Match ID 18Char']], flat_df], axis=1)

# Step 5: Ensure all columns are present and in the desired order
desired_columns = ['Match ID 18Char', 'date', 'green_flag_count', 'red_flag_count'] + columns
df_final = df_final.reindex(columns=desired_columns).fillna(0)

# Step 6: Display the result
print(df_final)

# Step 7: Save to Excel (optional)
df_final.to_excel('Apr3TrainRun1LLMFlattened1.xlsx', index=False)

          Match ID 18Char        date  green_flag_count  red_flag_count  \
0      a1v2J0000027CWsQAM  2017-12-20                 2               0   
1      a1v2J0000027CWsQAM  2018-01-19                 2               0   
2      a1v2J0000027CWsQAM  2018-02-18                 2               0   
3      a1v2J0000027CWsQAM  2018-03-20                 2               0   
4      a1v2J0000027CWsQAM  2018-04-19                 2               0   
...                   ...         ...               ...             ...   
25045  a1v2J0000038jRgQAI  2023-11-03                 1               0   
25046  a1v2J0000038jRgQAI  2024-02-01                 1               0   
25047  a1v2J0000038jRgQAI  2024-06-30                 1               0   
25048  a1v2J0000038jRgQAI  2024-09-19                 1               0   
25049  a1v2J0000038jRgQAI  2024-12-04                 1               0   

       Match closure Discussed  Changing Match Type  COVID impact  \
0                            0

In [109]:
merged_df.to_excel('combined_notes.xlsx', index=False)
error_df.head(5)

Empty DataFrame
Columns: [Match ID 18Char, QueryStr, Error]
Index: []

In [172]:
import pandas as pd
import json
import ast  # For safely evaluating string literals

# Load your DataFrame from Excel
df_sorted = pd.read_excel('combined_notes.xlsx')

# Full list of event columns
event_columns = [
    'Match closure Discussed', 'Changing Match Type', 'COVID impact',
    'Child/Family: Feels incompatible with volunteer', 'Child/Family: Moved',
    'Child/Family: Lost contact with agency', 'Child/Family: Lost contact with volunteer/agency',
    'Child/Family: Lost contact with volunteer', 'Child/Family: Moved out of service',
    'Child/Family: Unrealistic expectations', 'Child/Family: Time constraints',
    'Child/Family: Infraction of match rules/agency policies', 'Child/Family: Moved within service area',
    'Child: Graduated', 'Child: Transportation Issues', 'Child: Changed school/site',
    'Child: Lost interest', 'Child: Family structure changed', 'Child: Severity of challenges',
    'Volunteer: Transportation Issues', 'Volunteer: Moved out of service area',
    'Volunteer: Moved within service area', 'Volunteer: Lost contact with agency',
    'Volunteer: Lost contact with child/agency', 'Volunteer: Feels incompatible with child/family',
    'Volunteer: Time constraint', 'Volunteer: Deceased', 'Volunteer: Lost contact with child/family',
    'Volunteer: Infraction of match rules/agency policies', 'Volunteer: Unrealistic expectations',
    'Volunteer: Pregnancy', 'Volunteer: Changed workplace/school partnership',
    'Agency: Challenges with program/partnership', 'Agency: Concern with Volunteer re: child safety'
]

# Function to expand JSON response for a single row
def expand_json_row(row):
    json_data = row['JSON Response']
    # Handle empty or invalid JSON responses
    if pd.isna(json_data) or not json_data or (isinstance(json_data, list) and not json_data):
        # Return a single row with default values if JSON is empty or NaN
        df_json = pd.DataFrame([{'date': pd.NA, 'green_flag_count': 0, 'red_flag_count': 0, 'events': {}}])
    else:
        # If json_data is a string, try parsing it as a Python literal first, then as JSON
        if isinstance(json_data, str):
            try:
                # Try to evaluate it as a Python literal (e.g., "[{'date': ...}]")
                json_data = ast.literal_eval(json_data)
            except (ValueError, SyntaxError):
                try:
                    # If that fails, try parsing it as JSON (e.g., '[{"date": ...}]')
                    json_data = json.loads(json_data)
                except json.JSONDecodeError:
                    # If both fail, log the error and return a default row
                    print(f"Warning: Could not parse JSON Response for Match ID {row['Match ID 18Char']}: {json_data}")
                    df_json = pd.DataFrame([{'date': pd.NA, 'green_flag_count': 0, 'red_flag_count': 0, 'events': {}}])
                    # Duplicate original columns and return early
                    original_cols = {col: row[col] for col in df_sorted.columns if col != 'JSON Response'}
                    for col, value in original_cols.items():
                        df_json[col] = value
                    return df_json.fillna(0)
        # If json_data is already a list, use it directly
        df_json = pd.DataFrame(json_data)
    
    # Expand the 'events' dictionary
    df_events = pd.json_normalize(df_json['events'])
    df_expanded = pd.concat([df_json[['date', 'green_flag_count', 'red_flag_count']], df_events], axis=1)
    
    # Ensure all event columns are present
    for col in event_columns:
        if col not in df_expanded.columns:
            df_expanded[col] = 0
    
    # Duplicate the original row's other columns for each date
    original_cols = {col: row[col] for col in df_sorted.columns if col != 'JSON Response'}
    for col, value in original_cols.items():
        df_expanded[col] = value
    
    return df_expanded.fillna(0)

# Step 1: Apply the expansion to each row in df_sorted
expanded_dfs = [expand_json_row(row) for _, row in df_sorted.iterrows()]
df_expanded = pd.concat(expanded_dfs, ignore_index=True)

# Step 2: Convert 'date' to datetime for sorting
df_expanded['date'] = pd.to_datetime(df_expanded['date'], errors='coerce')

# Step 3: Sort by date
df_expanded = df_expanded.sort_values('date', ascending=True)

# Step 4: Get the last 5 rows per 'Match ID 18Char'
df_last_5 = df_expanded.groupby('Match ID 18Char').tail(5)

# Step 5: Reorder columns
base_columns = ['Match ID 18Char', 'Rationale for Match', 'Dated Short Notes']
final_columns = base_columns + ['date', 'green_flag_count', 'red_flag_count'] + event_columns
df_final = df_last_5[final_columns]

# Step 6: Display the result
print(df_final)

# Step 7: Save to Excel
df_final.to_excel('expanded_json_data.xlsx', index=False)

KeyError: 'events'

In [108]:
# Testing area

testinput = '''
```json
fdfsdjfks
  
'''


def parse_json_message_test(json_string: str) -> List[Dict[str, Any]]:
    
    try:
        brace_position = json_string.index('[')
        json_string = json_string[brace_position:]
    except:
        raise ValueError("Input does not start with '[': invalid JSON array format.")
        

    while True:
        if not json_string:
            raise ValueError("Couldn't fix JSON")
        try:
            data = json.loads(json_string + "]")
        except json.decoder.JSONDecodeError:
            json_string = json_string[:-1]
            continue
        break
    return data

print(parse_json_message_test(testinput))

ValueError: Input does not start with '[': invalid JSON array format.

In [62]:
# Grok 2 model using auto parse
context_new = '''
Follow prompt instruction explicitly without exceptions. You are a machine processing text. Your only task is to identify potential events, green flags (e.g., factors likely to enhance relationship quality and duration) and red flags (e.g., risks of early termination or poor outcomes) in the mentorship program by big brothers big sisters of america.

Background:
BBB or Agency = Big brothers’ big sisters of America organization
LB/LS = Little Brother/Sister (Mentee Or Child)
BB/BS = Big Brother/Sister (Mentor Or Volunteer)
MEC or MSC = Match coordinator from BBB
PG = Parent of LB/LS
Current Service area = Minnesota

Flags :
Green Flag indicates any events falling near to the categories below ,
with a positive impact on match
Red Flag indicates any events falling near to the categories below ,
with a negative impact on match

Green Flags to Detect:
Any positive Events identified in the Rationale for Match
Indication that Mentor completed BBB training pre-match
Commitment to 18-month match
Shared interests/preferences in match
Monthly in-person/phone support from agency to mentor, youth, parent
High mentor satisfaction, realistic expectations
Youth reports positive relationship, frequent meetings
Demographic alignment (race, gender, religion)
Close geographic proximity or good transportation access
Positive youth traits (competence, confidence, connection, care, character)
Older, experienced mentor with empathy, flexibility, multicultural competence
Younger mentee (elementary–early adolescence), good relational history

Red Flags to Detect:
No pre-match training or ongoing support
Mismatched interests, ignored mentor preferences
Infrequent/superficial staff check-ins (<6 min)
Mentor frustration, unrealistic expectations, youth resistance
No closure plan for early termination
Match ends <6 months (34–50% risk)
Younger mentor (18–25), negative attitudes, low commitment
Older mentee seeking autonomy, severe risk factors
No monthly staff support (email-only contact)
Inadequate BBB training, excessive/scanty staff involvement
Parental dissatisfaction/interference
Match ends <13–18 months

Save count of green flags and count of red flags in the JSON output later
'''

output_new = '''

In the JSON below, events are defined below:
•Match closure Discussed
•Changing Match Type
•COVID impact
•Child/Family: Feels incompatible with volunteer
•Child/Family: Moved
•Child/Family: Lost contact with agency
•Child/Family: Lost contact with volunteer/agency
•Child/Family: Lost contact with volunteer
•Child/Family: Moved out of service 
•Child/Family: Unrealistic expectationsarea
•Child/Family: Time constraints
•Child/Family: Infraction of match rules/agency policies
•Child/Family: Moved within service area
•Child: Graduated
•Child: Transportation Issues
•Child: Changed school/site
•Child: Lost interest
•Child: Family structure changed
•Child: Severity of challenges
•Volunteer: Transportation Issues
•Volunteer: Moved out of service area
•Volunteer: Moved within service area
•Volunteer: Lost contact with agency
•Volunteer: Lost contact with child/agency
•Volunteer: Feels incompatible with child/family
•Volunteer: Time constraint
•Volunteer: Deceased
•Volunteer: Lost contact with child/family
•Volunteer: Infraction of match rules/agency policies
•Volunteer: Unrealistic expectations
•Volunteer: Pregnancy
•Volunteer: Changed workplace/school partnership
•Agency: Challenges with program/partnership
•Agency: Concern with Volunteer re: child safety

Always return a valid JSON response for each date:
[
  {
    "date": "YYYY-MM-DD",
    "green_flag_count": <number>
    "red_flag_count ": <number>
    "events": {
      "Child/Family: Unrealistic expectations": <score>,
      "Volunteer: Unrealistic expectations": <score>,
      ......
    }
  },
]


Critical Instructions:
Generate multiple JSON object for each date in the original text.
"Events" field shall be the same as above.
Exclude non-occurring events: Only include event types present on a given date.
Severity scores: Assign scores (0–5) to each event type (e.g., "Volunteer: Time constraint_severity"), using your best judgement where 1 is little impact, and 5 is implicates an immediate end to the match.
Exclude events where Severity == 0
Output format: JSON with "date" and "events" containing event-specific severity scores, "event_count".
The response must not exceed 1000 tokens.
If the full JSON exceeds 1000 tokens, trim earlier dates and include only the most recent dates, starting from the latest date and working backward, until the output fits within 1000 tokens.
Do not include any explanatory text or additional content beyond the JSON unless it fits within the token limit.
Assume 1 token ≈ 4 characters (including spaces and punctuation) for token estimation.

'''
count = 0


import os
from typing import List, Optional
from pydantic import BaseModel, Field
from openai import OpenAI
import pandas as pd
import json
from datetime import date
from typing import Dict, Any

class EventItem(BaseModel):
    Item: str = Field(description="Description of the item or service")
    severity: int = Field(description="Number of units", ge=1)

class ContentModel(BaseModel):
    green_flag_count: int = Field(description="Count of green flags indicating positive outcomes")
    red_flag_count: int = Field(description="Count of red flags indicating issues or concerns")
    features: List[EventItem] = Field(description="Dictionary of event types and their severity scores (0-5), plus counts")

class ResponseModel(BaseModel):
    date: str = Field(description="Dates of Catchup")
    content: List[ContentModel] = Field(description="Content by date")
        
        
count = 0

def process_grok_queries(query_str: str) -> ResponseModel:

    global count
    
    # Retrieve the API key from the environment variable
    api_key = os.getenv("XAI_API_KEY")
    if not api_key:
        raise ValueError("XAI_API_KEY environment variable is not set.")

    # Initialize the OpenAI client with the Grok API base URL and API key
    client = OpenAI(
        api_key=api_key,
        base_url="https://api.x.ai/v1"
    )
    
    user_content = context + " Dated Match Notes: " + str(query_str) + output
    
    
    messages = [
        {"role": "user", "content":context_new + query_str + output_new}
    ]
        
    completion = client.beta.chat.completions.parse(
        model="grok-2-latest",
        messages= messages,
        response_format=ResponseModel,
    )
    
    response_model = completion.choices[0].message.parsed
    
    # Telementry
    count += 1
    
    print(f"---------------------------------------------------")
    print("Processed: " + str(count))
    print(f"Raw Response: {completion.choices[0].message.content}")
    print(f"---------------------------------------------------")
    print(f"Converted to dict: {response_model.dict()}")

    return response_model

def process_dataframe_queries(df: pd.DataFrame):

    df['ParsedResponse'] = None 
    
    # Process each row
    for index, row in df.iterrows():
        query_str = row["QueryStr"]
        response = process_grok_queries(query_str)
        df.at[index, 'ParsedResponse'] = response  # Assign the response to the new column
    
    return df


processed_df = process_dataframe_queries(merged_df)
processed_df.head(10)


---------------------------------------------------
Processed: 1
Raw Response: {
  "date": "2025-02-13",
  "content": [
    {
      "green_flag_count": 1,
      "red_flag_count": 0,
      "features": [
        {
          "Item": "Child: Graduated",
          "severity": 1
        }
      ]
    }
  ]
}
---------------------------------------------------
Converted to dict: {'date': '2025-02-13', 'content': [{'green_flag_count': 1, 'red_flag_count': 0, 'features': [{'Item': 'Child: Graduated', 'severity': 1}]}]}


C:\Users\user\AppData\Local\Temp\ipykernel_41916\3758889445.py:178: PydanticDeprecatedSince20: The `dict` method is deprecated; use `model_dump` instead. Deprecated in Pydantic V2.0 to be removed in V3.0. See Pydantic V2 Migration Guide at https://errors.pydantic.dev/2.11/migration/
  print(f"Converted to dict: {response_model.dict()}")


---------------------------------------------------
Processed: 2
Raw Response: {
  "date": "2022-02-11",
  "content": [
    {
      "green_flag_count": 0,
      "red_flag_count": 10,
      "features": [
        {
          "Item": "Child/Family: Feels incompatible with volunteer",
          "severity": 1
        },
        {
          "Item": "Child/Family: Infraction of match rules/agency policies",
          "severity": 1
        },
        {
          "Item": "Volunteer: Infraction of match rules/agency policies",
          "severity": 1
        },
        {
          "Item": "Child: Lost interest",
          "severity": 1
        },
        {
          "Item": "Child: Severity of challenges",
          "severity": 1
        },
        {
          "Item": "Match closure Discussed",
          "severity": 1
        },
        {
          "Item": "Agency: Challenges with program/partnership",
          "severity": 1
        },
        {
          "Item": "Volunteer: Feels incompatible 

Match ID 18Char                                Rationale for Match  \
0  a1v2J0000027dtOQAQ  B_first_name and L_first_name were matched bec...   
1  a1v2J000002uR0JQAU  Their shared interests include spending time o...   
2  a1v2J0000039UeRQAU  Distance: 9 miles, 15-20 min Shared Traits: Pa...   
3  a1v2J000003Ef9jQAC  1. Distance: 14 miles (18 mins) 2. Shared Trai...   
4  a1v2J0000027NsOQAU                                                NaN   
5  a1v2J0000028pRvQAI                                                NaN   

                                    Closure Reason  \
0                                              NaN   
1  Child/Family: Feels incompatible with volunteer   
2                                 Volunteer: Moved   
3                                              NaN   
4                                 Volunteer: Moved   
5                                Volunteer: Health   

                                     Closure Details  \
0                                                NaN   
1  MATCH CLOSURE SUMMARY Describe the reasons for...   
2  Match Closure Details Describe the reasons for...   
3                                                NaN   
4                                                NaN   
5                                                NaN   

                                   Dated Short Notes  \
0  2018-02-14 Question: Activities: Answer: See n...   
1  2018-04-30 Question: Activities: Answer: - Que...   
2  2020-01-10 Match attended January MCP. Matches...   
3  2021-04-27 Match registered for BBBS event: Ci...   
4  2017-04-10 Question: Activities: Answer: MSC a...   
5  2017-03-30 Question: Activities: Answer: Msc a...   

                                            QueryStr  \
0  Match Rationale: B_first_name and L_first_name...   
1  Match Rationale: Their shared interests includ...   
2  Match Rationale: Distance: 9 miles, 15-20 min ...   
3  Match Rationale: 1. Distance: 14 miles (18 min...   
4  Match Rationale: nan Dated Notes: 2017-04-10 Q...   
5  Match Rationale: nan Dated Notes: 2017-03-30 Q...   

                                       JSON Response  \
0  {'answer': '```json
[
  {
    "date": "2024-01...   
1  {'answer': '```json
[
  {
    "date": "2022-02...   
2  {'answer': '```json
[
  {
    "date": "2020-01...   
3  {'answer': '```json
[
  {
    "date": "2023-11...   
4  {'answer': '```json
[
  {
    "date": "2017-04...   
5  {'answer': '```json
[
  {
    "date": "2017-03...   

                                      ParsedResponse  
0  date='2025-02-13' content=[ContentModel(green_...  
1  date='2022-02-11' content=[ContentModel(green_...  
2  date='2020-01-10' content=[ContentModel(green_...  
3  date='2021-04-27' content=[ContentModel(green_...  
4  date='2017-04-10' content=[ContentModel(green_...  
5  date='2017-03-30' content=[ContentModel(green_...